1. https://towardsdatascience.com/shap-explain-any-machine-learning-model-in-python-24207127cad7
2. https://towardsdatascience.com/introduction-to-shap-with-python-d27edc23c454

In [1]:
import shap
import pandas as pd
import joblib
import matplotlib.pyplot as plt
from PIL import Image
from io import BytesIO

In [2]:
test_data = pd.read_csv('SHP2_test_descriptors_150.csv')
test_data

SMILES  MaxEStateIndex  \
0                O=C(C(C=C1O)=CC2=CC=C(O)C(O)=C2C1=O)O       11.762075   
1               O=C(C(C=C1O)=CC2=CC=C(O)C(O)=C2C1=O)OC       11.891220   
2              O=C(C(C=C1O)=CC2=CC=C(O)C(O)=C2C1=O)OCC       11.960761   
3           O=C(C(C=C1O)=CC2=CC=C(O)C(O)=C2C1=O)OC(C)C       12.025094   
4                O=C(C(C=C1O)=CC2=CC=C(O)C(O)=C2C1=O)N       11.802891   
..                                                 ...             ...   
145  O=C(NC1=CC=CC=C1[N+]([O-])=O)CCN(C(C)=NC2=C3C4...       12.993000   
146  O=C(C1=CC2=C(N(C)C(C3=CC=CC=C3)=C2C4=CN(CCC(NC...       12.357815   
147  O=C(C1=CC2=C(N(C)C(C3=CC=CC=C3)=C2C4=CN(CC(NC5...       12.847668   
148  O=C(C1=CC2=C(N(C)C(C3=CC=CC=C3)=C2C4=CN(CCC(NC...       12.712730   
149  O=C(C1=CC2=C(N(C)C(C3=CC=CC=C3)=C2C4=CN(CCCC(N...       12.621895   

     MinEStateIndex  MaxAbsEStateIndex  MinAbsEStateIndex       qed    MolWt  \
0         -1.324292          11.762075           0.104630  0.559777  248.190   
1         -0.890229          11.891220           0.044269  0.524898  262.217   
2         -0.885233          11.960761           0.026352  0.566824  276.244   
3         -0.887040          12.025094           0.029269  0.576007  290.271   
4         -0.897315          11.802891           0.078991  0.543863  247.206   
..              ...                ...                ...       ...      ...   
145       -0.542407          12.993000           0.020148  0.524557  398.444   
146       -1.223568          12.357815           0.143555  0.313800  481.512   
147       -1.238342          12.847668           0.069408  0.233485  543.583   
148       -1.227003          12.712730           0.156276  0.204736  557.610   
149       -1.218025          12.621895           0.088681  0.179894  571.637   

     HeavyAtomMolWt  ExactMolWt  NumValenceElectrons  ...  fr_sulfone  \
0           240.126  248.032088                   92  ...           0   
1           252.137  262.047738                   98  ...           0   
2           264.148  276.063388                  104  ...           0   
3           276.159  290.079038                  110  ...           0   
4           238.134  247.048072                   92  ...           0   
..              ...         ...                  ...  ...         ...   
145         380.300  398.104876                  144  ...           0   
146         458.328  481.175004                  180  ...           0   
147         518.383  543.190654                  202  ...           0   
148         530.394  557.206304                  208  ...           0   
149         542.405  571.221954                  214  ...           0   

     fr_term_acetylene  fr_tetrazole  fr_thiazole  fr_thiocyan  fr_thiophene  \
0                    0             0            0            0             0   
1                    0             0            0            0             0   
2                    0             0            0            0             0   
3                    0             0            0            0             0   
4                    0             0            0            0             0   
..                 ...           ...          ...          ...           ...   
145                  0             0            0            0             1   
146                  0             0            0            0             0   
147                  0             0            0            0             0   
148                  0             0            0            0             0   
149                  0             0            0            0             0   

     fr_unbrch_alkane  fr_urea  IC50(microM)  TARGET  
0                   0        0         0.097       1  
1                   0        0         0.161       1  
2                   0        0         0.985       1  
3                   0        0          4.87       0  
4                   0        0          4.11       0  
..                ...      ...

In [3]:
test_data['TARGET'].value_counts()

0    117
1     33
Name: TARGET, dtype: int64

In [4]:
final_features = ['MaxPartialCharge', 'FpDensityMorgan2', 'BCUT2D_CHGLO', 'BCUT2D_MRHI',
       'PEOE_VSA12', 'PEOE_VSA6', 'SMR_VSA3', 'SlogP_VSA3', 'SlogP_VSA8',
       'EState_VSA6', 'NumHAcceptors', 'NumSaturatedCarbocycles',
       'fr_bicyclic', 'TARGET']

In [5]:
test_data = test_data[final_features]
test_data

MaxPartialCharge  FpDensityMorgan2  BCUT2D_CHGLO  BCUT2D_MRHI  \
0            0.335343          1.666667     -1.988112     5.961393   
1            0.337506          1.789474     -1.993067     5.968264   
2            0.337772          1.850000     -2.002685     5.968802   
3            0.338038          1.761905     -2.062196     5.969423   
4            0.248358          1.722222     -1.988933     5.984624   
..                ...               ...           ...          ...   
145          0.292242          2.142857     -2.102211     7.184306   
146          0.338995          1.694444     -2.066425     6.071176   
147          0.338995          1.487805     -2.071661     6.071856   
148          0.338995          1.500000     -2.071839     6.071461   
149          0.338995          1.511628     -2.071673     6.071368   

     PEOE_VSA12  PEOE_VSA6   SMR_VSA3  SlogP_VSA3  SlogP_VSA8  EState_VSA6  \
0       5.42879   6.066367   0.000000    0.000000   10.772448     0.000000   
1       5.42879   6.066367   0.000000    4.736863   10.772448     0.000000   
2       5.42879   6.066367   0.000000    4.736863   10.772448     6.923737   
3       5.42879   6.066367   0.000000    4.736863   10.772448    13.847474   
4      11.33597   6.066367   0.000000    0.000000   10.772448     0.000000   
..          ...        ...        ...         ...         ...          ...   
145     5.90718  12.132734   9.551078   24.180937   10.216621    24.326890   
146     5.90718  53.744322  19.560969   18.386966   33.417684    10.878647   
147     5.90718  78.009790  19.560969   18.386966   44.544587     6.196844   
148     5.90718  78.009790  19.560969   18.386966   44.544587    10.878647   
149     5.90718  78.009790  19.560969   18.386966   44.544587    10.878647   

     NumHAcceptors  NumSaturatedCarbocycles  fr_bicyclic  TARGET  
0                5                        0            1       1  
1                6                        0            1       1  
2                6                        0            1       1  
3                6                        0            1       0  
4                5                        0            1       0  
..             ...                      ...          ...     ...  
145              7                        0            3       0  
146              7                        0            1       0  
147              7                        0            1       0  
148              7                        0            1       0  
149              7                        0            1       0  

[150 rows x 14 columns]

In [6]:
X_test = test_data.iloc[:,:-1]
y_test = test_data.iloc[:,-1]

In [7]:
X_test

MaxPartialCharge  FpDensityMorgan2  BCUT2D_CHGLO  BCUT2D_MRHI  \
0            0.335343          1.666667     -1.988112     5.961393   
1            0.337506          1.789474     -1.993067     5.968264   
2            0.337772          1.850000     -2.002685     5.968802   
3            0.338038          1.761905     -2.062196     5.969423   
4            0.248358          1.722222     -1.988933     5.984624   
..                ...               ...           ...          ...   
145          0.292242          2.142857     -2.102211     7.184306   
146          0.338995          1.694444     -2.066425     6.071176   
147          0.338995          1.487805     -2.071661     6.071856   
148          0.338995          1.500000     -2.071839     6.071461   
149          0.338995          1.511628     -2.071673     6.071368   

     PEOE_VSA12  PEOE_VSA6   SMR_VSA3  SlogP_VSA3  SlogP_VSA8  EState_VSA6  \
0       5.42879   6.066367   0.000000    0.000000   10.772448     0.000000   
1       5.42879   6.066367   0.000000    4.736863   10.772448     0.000000   
2       5.42879   6.066367   0.000000    4.736863   10.772448     6.923737   
3       5.42879   6.066367   0.000000    4.736863   10.772448    13.847474   
4      11.33597   6.066367   0.000000    0.000000   10.772448     0.000000   
..          ...        ...        ...         ...         ...          ...   
145     5.90718  12.132734   9.551078   24.180937   10.216621    24.326890   
146     5.90718  53.744322  19.560969   18.386966   33.417684    10.878647   
147     5.90718  78.009790  19.560969   18.386966   44.544587     6.196844   
148     5.90718  78.009790  19.560969   18.386966   44.544587    10.878647   
149     5.90718  78.009790  19.560969   18.386966   44.544587    10.878647   

     NumHAcceptors  NumSaturatedCarbocycles  fr_bicyclic  
0                5                        0            1  
1                6                        0            1  
2                6                        0            1  
3                6                        0            1  
4                5                        0            1  
..             ...                      ...          ...  
145              7                        0            3  
146              7                        0            1  
147              7                        0            1  
148              7                        0            1  
149              7                        0            1  

[150 rows x 13 columns]

In [8]:
model = joblib.load('XGB_Final.pkl')

In [9]:
explainer = shap.Explainer(model)
shap_values = explainer(X_test)

ntree_limit is deprecated, use `iteration_range` or model slicing instead.


# SHAP Waterfall Plot

In [10]:
plt.figure(figsize=(10,10), dpi=1200) 
shap.plots.waterfall(shap_values[0],show=False)
plt.savefig('.\images\SHAP_VALUE_true_weak_inhibitor.png')

In [11]:
plt.figure(figsize=(10,10), dpi=1200)
shap.plots.waterfall(shap_values[3],show=False)
plt.savefig('.\images\SHAP_VALUE_true_strong_inhibitor.png')

# SHAP Summary Plot

In [12]:
plt.figure(figsize=(10,10), dpi=1200)
shap.summary_plot(shap_values, X_test,show=False)
plt.savefig('.\images\summary_plot.png')

# SHAP Bar Plot

In [14]:
plt.figure(figsize=(10,10), dpi=1200)
shap.plots.bar(shap_values,show=False)
plt.savefig(r'.\images\feature_importance.png')